In this repo, I will use Feature Engineer techniques, I have learned in Feature Engineering practices, to improve predictive power for House Prices problems

### Set up notebook environment

In [2]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
from IPython.display import display

#set Matplotlib defaults
plt.style.use('seaborn-v0_8-whitegrid')
plt.rc('figure', autolayout=True)
plt.rc(
    "axes",
    labelweight='bold',
    labelsize='large',
    titleweight='bold',
    titlesize=14,
    titlepad=10,)

In [3]:
pd.set_option('display.max_columns', None) #showing all columns
pd.set_option("display.max_rows", None) #show all rows

In [4]:
#loading description file
discription_file = "./house-prices-advanced-regression-techniques/data_description.txt"
with open(discription_file) as f:
    contents = f.read()
    print(contents)

MSSubClass: Identifies the type of dwelling involved in the sale.	

        20	1-STORY 1946 & NEWER ALL STYLES
        30	1-STORY 1945 & OLDER
        40	1-STORY W/FINISHED ATTIC ALL AGES
        45	1-1/2 STORY - UNFINISHED ALL AGES
        50	1-1/2 STORY FINISHED ALL AGES
        60	2-STORY 1946 & NEWER
        70	2-STORY 1945 & OLDER
        75	2-1/2 STORY ALL AGES
        80	SPLIT OR MULTI-LEVEL
        85	SPLIT FOYER
        90	DUPLEX - ALL STYLES AND AGES
       120	1-STORY PUD (Planned Unit Development) - 1946 & NEWER
       150	1-1/2 STORY PUD - ALL AGES
       160	2-STORY PUD - 1946 & NEWER
       180	PUD - MULTILEVEL - INCL SPLIT LEV/FOYER
       190	2 FAMILY CONVERSION - ALL STYLES AND AGES

MSZoning: Identifies the general zoning classification of the sale.
		
       A	Agriculture
       C	Commercial
       FV	Floating Village Residential
       I	Industrial
       RH	Residential High Density
       RL	Residential Low Density
       RP	Residential Low Density Park 
       RM

#### loading data

In [5]:
df_pretrain = pd.read_csv("./house-prices-advanced-regression-techniques/train.csv", index_col="Id")
df_pretest = pd.read_csv("./house-prices-advanced-regression-techniques/test.csv", index_col="Id")
df = pd.concat([df_pretrain, df_pretest])
print(df.shape)
df.head(5)

(2919, 80)


MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
Id                                                                    
1           60       RL         65.0     8450   Pave   NaN      Reg   
2           20       RL         80.0     9600   Pave   NaN      Reg   
3           60       RL         68.0    11250   Pave   NaN      IR1   
4           70       RL         60.0     9550   Pave   NaN      IR1   
5           60       RL         84.0    14260   Pave   NaN      IR1   

   LandContour Utilities LotConfig LandSlope Neighborhood Condition1  \
Id                                                                     
1          Lvl    AllPub    Inside       Gtl      CollgCr       Norm   
2          Lvl    AllPub       FR2       Gtl      Veenker      Feedr   
3          Lvl    AllPub    Inside       Gtl      CollgCr       Norm   
4          Lvl    AllPub    Corner       Gtl      Crawfor       Norm   
5          Lvl    AllPub       FR2       Gtl      NoRidge       Norm   

   Condition2 BldgType HouseStyle  OverallQual  OverallCond  YearBuilt  \
Id                                                                       
1        Norm     1Fam     2Story            7            5       2003   
2        Norm     1Fam     1Story            6            8       1976   
3        Norm     1Fam     2Story            7            5       2001   
4        Norm     1Fam     2Story            7            5       1915   
5        Norm     1Fam     2Story            8            5       2000   

    YearRemodAdd RoofStyle RoofMatl Exterior1st Exterior2nd MasVnrType  \
Id                                                                       
1           2003     Gable  CompShg     VinylSd     VinylSd    BrkFace   
2           1976     Gable  CompShg     MetalSd     MetalSd        NaN   
3           2002     Gable  CompShg     VinylSd     VinylSd    BrkFace   
4           1970     Gable  CompShg     Wd Sdng     Wd Shng        NaN   
5           2000     Gable  CompShg     VinylSd     VinylSd    BrkFace   

    MasVnrArea ExterQual ExterCond Foundation BsmtQual BsmtCond BsmtExposure  \
Id                                                                             
1        196.0        Gd        TA      PConc       Gd       TA           No   
2          0.0        TA        TA     CBlock       Gd       TA           Gd   
3        162.0        Gd        TA      PConc       Gd       TA           Mn   
4          0.0        TA        TA     BrkTil       TA       Gd           No   
5        350.0        Gd        TA      PConc       Gd       TA           Av   

   BsmtFinType1  BsmtFinSF1 BsmtFinType2  BsmtFinSF2  BsmtUnfSF  TotalBsmtSF  \
Id                                                                             
1           GLQ       706.0          Unf         0.0      150.0        856.0   
2           ALQ       978.0          Unf         0.0      284.0       1262.0   
3           GLQ       486.0          Unf         0.0      434.0        920.0   
4           ALQ       216.0          Unf         0.0      540.0        756.0   
5           GLQ       655.0          Unf         0.0      490.0       1145.0   

   Heating HeatingQC CentralAir Electrical  1stFlrSF  2ndFlrSF  LowQualFinSF  \
Id                                                                             
1     GasA        Ex          Y      SBrkr       856       854             0   
2     GasA        Ex          Y      SBrkr      1262         0             0   
3     GasA        Ex          Y      SBrkr       920       866             0   
4     GasA        Gd          Y      SBrkr       961       756             0   
5     GasA        Ex          Y      SBrkr      1145      1053             0   

    GrLivArea  BsmtFullBath  BsmtHalfBath  FullBath  HalfBath  BedroomAbvGr  \
Id                                                                            
1        1710           1.0           0.0         2         1             3   
2        1262           0.0           1.0  

#### preprocessing data

In [6]:
#Examine the features
#the loop will go through each features and it's values
#enter space to keep go through each features, enter 'break' to exit
print(f"There are {df.shape[1]} columns")
for col in df.columns:
    enter = input()
    if enter == "break": #exit loop
        break
    else:
        print(f"{col} - {df[col].dtype}:", df[col].unique())

There are 80 columns

MSSubClass - int64: [ 60  20  70  50 190  45  90 120  30  85  80 160  75 180  40 150]

MSZoning - object: ['RL' 'RM' 'C (all)' 'FV' 'RH' nan]

LotFrontage - float64: [ 65.  80.  68.  60.  84.  85.  75.  nan  51.  50.  70.  91.  72.  66.
 101.  57.  44. 110.  98.  47. 108. 112.  74. 115.  61.  48.  33.  52.
 100.  24.  89.  63.  76.  81.  95.  69.  21.  32.  78. 121. 122.  40.
 105.  73.  77.  64.  94.  34.  90.  55.  88.  82.  71. 120. 107.  92.
 134.  62.  86. 141.  97.  54.  41.  79. 174.  99.  67.  83.  43. 103.
  93.  30. 129. 140.  35.  37. 118.  87. 116. 150. 111.  49.  96.  59.
  36.  56. 102.  58.  38. 109. 130.  53. 137.  45. 106. 104.  42.  39.
 144. 114. 128. 149. 313. 168. 182. 138. 160. 152. 124. 153.  46.  26.
  25. 119.  31.  28. 117. 113. 125. 135. 136.  22. 123. 195. 155. 126.
 200. 131. 133.]

LotArea - int64: [ 8450  9600 11250 ...  1894 20000 10441]

Street - object: ['Pave' 'Grvl']
break


Investting every columns, we see there is typos in Exterior2nd mismatching with Exterior1st, and wrong assigned dtype - MSSubClass should be object not interger type, and those missing values (nan value) in some categorical columns, is actually absence, likes house with no basements, no pool, no garage, we will treat them right for better performance, for those in continous and discrete columns we need to impute

In [7]:
def cleaning_df(df): #function to clean our df
    df['Exterior2nd'] = df['Exterior2nd'].replace({"Brk Cmn" : "BrkComn"})
    #Some values of GarageYrBlt are corrupt, so we'll replace them with the year the house was built
    df['GarageYrBlt'] = df['GarageYrBlt'].where(df['GarageYrBlt'] <= 2010, df.YearBuilt)
    
    
    df.rename(columns={
        "1stFlrSF": "FirstFlrSF",
        "2ndFlrSF": "SecondFlrSF",
        "3SsnPorch": "Threeseasonporch",
    }, inplace=True,
    )
    return df

In [41]:
# The numeric features are already encoded correctly (`float` for
# continuous, `int` for discrete), but the categoricals we'll need to
# do ourselves. Note in particular, that the `MSSubClass` feature is
# read as an `int` type, but is actually a (nominative) categorical.

# The nominative (unordered) categorical features
features_nom = ["MSSubClass", "MSZoning", "Street", "Alley", "LandContour", "LotConfig", "Neighborhood", "Condition1", "Condition2", "BldgType", "HouseStyle", "RoofStyle", "RoofMatl", "Exterior1st", "Exterior2nd", "MasVnrType", "Foundation", "Heating", "CentralAir", "GarageType", "MiscFeature", "SaleType", "SaleCondition"]


# The ordinal (ordered) categorical features 

# Pandas calls the categories "levels"
five_levels = ["Po", "Fa", "TA", "Gd", "Ex"]
ten_levels = list(range(10))

ordered_levels = {
    "OverallQual": ten_levels,
    "OverallCond": ten_levels,
    "ExterQual": five_levels,
    "ExterCond": five_levels,
    "BsmtQual": five_levels,
    "BsmtCond": five_levels,
    "HeatingQC": five_levels,
    "KitchenQual": five_levels,
    "FireplaceQu": five_levels,
    "GarageQual": five_levels,
    "GarageCond": five_levels,
    "PoolQC": five_levels,
    "LotShape": ["Reg", "IR1", "IR2", "IR3"],
    "LandSlope": ["Sev", "Mod", "Gtl"],
    "BsmtExposure": ["No", "Mn", "Av", "Gd"],
    "BsmtFinType1": ["Unf", "LwQ", "Rec", "BLQ", "ALQ", "GLQ"],
    "BsmtFinType2": ["Unf", "LwQ", "Rec", "BLQ", "ALQ", "GLQ"],
    "Functional": ["Sal", "Sev", "Maj1", "Maj2", "Mod", "Min2", "Min1", "Typ"],
    "GarageFinish": ["Unf", "RFn", "Fin"],
    "PavedDrive": ["N", "P", "Y"],
    "Utilities": ["NoSeWa", "NoSewr", "AllPub"],
    "CentralAir": ["N", "Y"],
    "Electrical": ["Mix", "FuseP", "FuseF", "FuseA", "SBrkr"],
    "Fence": ["MnWw", "GdWo", "MnPrv", "GdPrv"],
}

# Add a None level for missing values
ordered_levels = {key: ["None"] + value for key, value in
                  ordered_levels.items()}


def encode(df):
    # Nominal categories
    for name in features_nom:
        df[name] = df[name].astype("category")
        # Add a None category for missing values
        if "None" not in df[name].cat.categories:
            df[name].cat.add_categories("None", inplace=True)
    # Ordinal categories
    for name, levels in ordered_levels.items():
        df[name] = df[name].astype(CategoricalDtype(levels,
                                                    ordered=True))
    return df

In [42]:
def imputing_df(df):
    #We'll impute 0 for missing numeric values and "None" for missing categorical values
    for name in df.select_dtypes("number"):
        df[name] = df[name].fillna(0)
    for name in df.select_dtypes("category"):
        df[name] = df[name].fillna("None")
    return df

In [46]:
def preprocessing_df(df, df_pretrain, df_pretest):
    df = cleaning_df(df)
    df = encoding_df(df)
    df = imputing_df(df)
    # Reform splits
    df_train = df.loc[df_pretrain.index, :]
    df_test = df.loc[df_pretest.index, :]
    return df_train, df_test

In [47]:
#loading data
df_train, df_test = preprocessing_df(df, df_pretrain, df_pretest)

In [48]:
display(df_train.info())

<class 'pandas.core.frame.DataFrame'>
Index: 1460 entries, 1 to 1460
Data columns (total 80 columns):
 #   Column            Non-Null Count  Dtype   
---  ------            --------------  -----   
 0   MSSubClass        1460 non-null   category
 1   MSZoning          1460 non-null   category
 2   LotFrontage       1460 non-null   float64 
 3   LotArea           1460 non-null   int64   
 4   Street            1460 non-null   category
 5   Alley             1460 non-null   category
 6   LotShape          1460 non-null   category
 7   LandContour       1460 non-null   category
 8   Utilities         1460 non-null   category
 9   LotConfig         1460 non-null   category
 10  LandSlope         1460 non-null   category
 11  Neighborhood      1460 non-null   category
 12  Condition1        1460 non-null   category
 13  Condition2        1460 non-null   category
 14  BldgType          1460 non-null   category
 15  HouseStyle        1460 non-null   category
 16  OverallQual       1460 non-nu

None

### Baseline Model
Baseline model will be used to compared with our later model with new features

In [49]:
# import libraries
from category_encoders import MEstimateEncoder
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.feature_selection import mutual_info_regression
from sklearn.model_selection import KFold, cross_val_score
from xgboost import XGBRegressor

In [50]:
# We can reuse this scoring function anytime we want to try out a new feature set.
def score_dataset(X, y, model=XGBRegressor()): #function compute the RMSLE scores for our models
    # Label encoding for categoricals
    #
    # Label encoding is good for XGBoost and RandomForest, but one-hot
    # would be better for models like Lasso or Ridge. The `cat.codes`
    # attribute holds the category levels.
    for colname in X.select_dtypes(["category"]):
        X[colname] = X[colname].cat.codes
    # Metric for Housing competition is RMSLE (Root Mean Squared Log Error)
    log_y = np.log(y)
    score = cross_val_score(
        model, X, log_y, cv=5, scoring="neg_mean_squared_error",
    )
    score = -1 * score.mean()
    score = np.sqrt(score)
    return score

In [51]:
X = df_train.copy()
y = X.pop("SalePrice")
# This baseline score helps us to know 
# whether some set of features we've assembled has actually led to any improvement or not
baseline_score = score_dataset(X, y)

print(f"Baseline score: {baseline_score:.5f} RMSLE")

Baseline score: 0.14302 RMSLE


### Feature Utility Scores

Use mutual information to compute a utility score for a feature, giving us an indication of how much potential the feature has


In [52]:
def make_mi_scores(X, y):
    X = X.copy()
    for colname in X.select_dtypes(["object", "category"]):
        X[colname], _ = X[colname].factorize()
    # All discrete features should now have integer dtypes
    discrete_features = [pd.api.types.is_integer_dtype(t) for t in X.dtypes]
    mi_scores = mutual_info_regression(X, y, discrete_features=discrete_features, random_state=0)
    mi_scores = pd.Series(mi_scores, name="MI Scores", index=X.columns)
    mi_scores = mi_scores.round(7)
    mi_scores = mi_scores.sort_values(ascending=False)
    return mi_scores

In [53]:
def plot_mi_scores(scores):
    scores = scores.sort_values(ascending=True)
    width = np.arange(len(scores))
    ticks = list(scores.index)
    plt.barh(width, scores)
    plt.yticks(width, ticks)
    plt.title("Mutual Information Scores")

In [54]:
#get mi score for our features
X = df_train.copy()
y = X.pop("SalePrice")

mi_scores = make_mi_scores(X, y)
mi_scores

OverallQual         0.571457
Neighborhood        0.526220
GrLivArea           0.430395
YearBuilt           0.407974
LotArea             0.394468
TotalBsmtSF         0.368536
GarageArea          0.361542
GarageCars          0.352312
BsmtQual            0.330803
KitchenQual         0.324680
ExterQual           0.324003
FirstFlrSF          0.282503
MSSubClass          0.281349
YearRemodAdd        0.274032
GarageYrBlt         0.272213
FullBath            0.263217
GarageFinish        0.262469
LotFrontage         0.218587
FireplaceQu         0.218161
GarageType          0.211553
TotRmsAbvGrd        0.208465
Foundation          0.191129
OpenPorchSF         0.190266
Fireplaces          0.172090
SecondFlrSF         0.167590
HeatingQC           0.164946
Exterior2nd         0.160257
BsmtFinSF1          0.154940
BsmtFinType1        0.153624
Exterior1st         0.133308
MSZoning            0.128241
BsmtUnfSF           0.119885
OverallCond         0.114790
WoodDeckSF          0.105387
MasVnrType    

we have a number of features that are highly informative and also some that don't seem to be informative at all (at least by themselves). The top scoring features will usually pay-off the most during feature development, so it could be a good idea to focus your efforts on those. On the other hand, training on uninformative features can lead to overfitting. So, the features with 0.0 scores we'll drop entirely

In [55]:
def drop_uninformative(df, mi_scores):
    return df.loc[:, mi_scores > 0.0]

In [56]:
X = df_train.copy()
y = X.pop("SalePrice")
X = drop_uninformative(X, mi_scores)

score_dataset(X, y)

0.14312932144357388

### Create Features
To make our feature engineering workflow more modular, we'll define a function that will take a prepared dataframe and pass it through a pipeline of transformations to get the final feature set

In [57]:
def create_features(df):
    X = df.copy()
    y = X.pop("SalePrice")
    X = X.join(create_features_1(X))
    X = X.join(create_features_2(X))
    X = X.join(create_features_3(X))
    # ...
    return X

def label_encode(df):
    X = df.copy()
    for colname in X.select_dtypes(["category"]):
        X[colname] = X[colname].cat.codes
    return X

A label encoding is okay for any kind of categorical feature when we're using a tree-ensemble like XGBoost, even for unordered categories. 
If we wanted to try a linear regression model (also popular in this competition), we would instead want to use a one-hot encoding, especially for the features with unordered categories.

#### other ways creating features 

In [58]:

def mathematical_transforms(df):
    X = pd.DataFrame()  # dataframe to hold new features
    X["LivLotRatio"] = df.GrLivArea / df.LotArea
    X["Spaciousness"] = (df.FirstFlrSF + df.SecondFlrSF) / df.TotRmsAbvGrd
    # This feature ended up not helping performance
    # X["TotalOutsideSF"] = \
    #     df.WoodDeckSF + df.OpenPorchSF + df.EnclosedPorch + \
    #     df.Threeseasonporch + df.ScreenPorch
    return X

def interactions(df):
    X = pd.get_dummies(df.BldgType, prefix="Bldg")
    X = X.mul(df.GrLivArea, axis=0)
    return X

def counts(df):
    X = pd.DataFrame()
    X["PorchTypes"] = df[[
        "WoodDeckSF",
        "OpenPorchSF",
        "EnclosedPorch",
        "Threeseasonporch",
        "ScreenPorch",
    ]].gt(0.0).sum(axis=1)
    return X

def break_down(df):
    X = pd.DataFrame()
    X["MSClass"] = df.MSSubClass.str.split("_", n=1, expand=True)[0]
    return X


def group_transforms(df):
    X = pd.DataFrame()
    X["MedNhbdArea"] = df.groupby("Neighborhood")["GrLivArea"].transform("median")
    return X

#### some ideas for other transforms you could explore:

* Interactions between the quality Qual and condition Cond features. OverallQual, for instance, was a high-scoring feature. You could try combining it with OverallCond by converting both to integer type and taking a product.
* Square roots of area features. This would convert units of square feet to just feet.
* Logarithms of numeric features. If a feature has a skewed distribution, applying a logarithm can help normalize it.
* Interactions between numeric and categorical features that describe the same thing. You could look at interactions between BsmtQual and TotalBsmtSF, for instance.
* Other group statistics in Neighboorhood. We did the median of GrLivArea. Looking at mean, std, or count could be interesting. You could also try combining the group statistics with other features. Maybe the difference of GrLivArea and the median is important?

#### K-Means clustering
unsupervised algorithm we will use to create features was k-means clustering. We could either use the cluster labels as a feature (a column with 0, 1, 2, ...) or we could use the distance of the observations to each cluster

In [59]:
cluster_features = [
    "LotArea",
    "TotalBsmtSF",
    "FirstFlrSF",
    "SecondFlrSF",
    "GrLivArea",
]


def cluster_labels(df, features, n_clusters=20):
    X = df.copy()
    X_scaled = X.loc[:, features]
    X_scaled = (X_scaled - X_scaled.mean(axis=0)) / X_scaled.std(axis=0)
    kmeans = KMeans(n_clusters=n_clusters, n_init=50, random_state=0)
    X_new = pd.DataFrame()
    X_new["Cluster"] = kmeans.fit_predict(X_scaled)
    return X_new


def cluster_distance(df, features, n_clusters=20):
    X = df.copy()
    X_scaled = X.loc[:, features]
    X_scaled = (X_scaled - X_scaled.mean(axis=0)) / X_scaled.std(axis=0)
    kmeans = KMeans(n_clusters=20, n_init=50, random_state=0)
    X_cd = kmeans.fit_transform(X_scaled)
    # Label features and join to dataset
    X_cd = pd.DataFrame(
        X_cd, columns=[f"Centroid_{i}" for i in range(X_cd.shape[1])]
    )
    return X_cd

PCA was the second unsupervised model we used for feature creation. The PCA algorithm gave us loadings which described each component of variation, and also the components which were the transformed datapoints. The loadings can suggest features to create and the components we can use as features directly.

Here are the utility functions from the PCA lesson:

In [60]:
def apply_pca(X, standardize=True):
    # Standardize
    if standardize:
        X = (X - X.mean(axis=0)) / X.std(axis=0)
    # Create principal components
    pca = PCA()
    X_pca = pca.fit_transform(X)
    # Convert to dataframe
    component_names = [f"PC{i+1}" for i in range(X_pca.shape[1])]
    X_pca = pd.DataFrame(X_pca, columns=component_names)
    # Create loadings
    loadings = pd.DataFrame(
        pca.components_.T,  # transpose the matrix of loadings
        columns=component_names,  # so the columns are the principal components
        index=X.columns,  # and the rows are the original features
    )
    return pca, X_pca, loadings

In [61]:
def plot_variance(pca, width=8, dpi=100):
    # Create figure
    fig, axs = plt.subplots(1, 2)
    n = pca.n_components_
    grid = np.arange(1, n + 1)
    # Explained variance
    evr = pca.explained_variance_ratio_
    axs[0].bar(grid, evr)
    axs[0].set(
        xlabel="Component", title="% Explained Variance", ylim=(0.0, 1.0)
    )
    # Cumulative Variance
    cv = np.cumsum(evr)
    axs[1].plot(np.r_[0, grid], np.r_[0, cv], "o-")
    axs[1].set(
        xlabel="Component", title="% Cumulative Variance", ylim=(0.0, 1.0)
    )
    # Set up figure
    fig.set(figwidth=8, dpi=100)
    return axs

In [62]:
def pca_inspired(df):
    #return features created by pca function 
    X = pd.DataFrame()
    X["Feature1"] = df.GrLivArea + df.TotalBsmtSF
    X["Feature2"] = df.YearRemodAdd * df.TotalBsmtSF
    return X

def pca_components(df, features):
    X = df.loc[:, features]
    _, X_pca, _ = apply_pca(X)
    return X_pca

pca_features = [
    "GarageArea",
    "YearRemodAdd",
    "TotalBsmtSF",
    "GrLivArea",
]

These are only a couple ways you could use the principal components. 

we could also try clustering using one or more components. 

NOTE: So clustering with the full set of components is the same as clustering with the original features. Instead, pick some subset of components, maybe those with the most variance or the highest MI scores.

For further analysis, you might want to look at a correlation matrix for the dataset:

In [67]:
df_train[df_train.columns]

MSSubClass  LotFrontage  LotArea Street Alley LotShape LandContour  \
Id                                                                        
1            60         65.0     8450   Pave  None      Reg         Lvl   
2            20         80.0     9600   Pave  None      Reg         Lvl   
3            60         68.0    11250   Pave  None      IR1         Lvl   
4            70         60.0     9550   Pave  None      IR1         Lvl   
5            60         84.0    14260   Pave  None      IR1         Lvl   
6            50         85.0    14115   Pave  None      IR1         Lvl   
7            20         75.0    10084   Pave  None      Reg         Lvl   
8            60          0.0    10382   Pave  None      IR1         Lvl   
9            50         51.0     6120   Pave  None      Reg         Lvl   
10          190         50.0     7420   Pave  None      Reg         Lvl   
11           20         70.0    11200   Pave  None      Reg         Lvl   
12           60         85.0    11924   Pave  None      IR1         Lvl   
13           20          0.0    12968   Pave  None      IR2         Lvl   
14           20         91.0    10652   Pave  None      IR1         Lvl   
15           20          0.0    10920   Pave  None      IR1         Lvl   
16           45         51.0     6120   Pave  None      Reg         Lvl   
17           20          0.0    11241   Pave  None      IR1         Lvl   
18           90         72.0    10791   Pave  None      Reg         Lvl   
19           20         66.0    13695   Pave  None      Reg         Lvl   
20           20         70.0     7560   Pave  None      Reg         Lvl   
21           60        101.0    14215   Pave  None      IR1         Lvl   
22           45         57.0     7449   Pave  Grvl      Reg         Bnk   
23           20         75.0     9742   Pave  None      Reg         Lvl   
24          120         44.0     4224   Pave  None      Reg         Lvl   
25           20          0.0     8246   Pave  None      IR1         Lvl   
26           20        110.0    14230   Pave  None      Reg         Lvl   
27           20         60.0     7200   Pave  None      Reg         Lvl   
28           20         98.0    11478   Pave  None      Reg         Lvl   
29           20         47.0    16321   Pave  None      IR1         Lvl   
30           30         60.0     6324   Pave  None      IR1         Lvl   
31           70         50.0     8500   Pave  Pave      Reg         Lvl   
32           20          0.0     8544   Pave  None      IR1         Lvl   
33           20         85.0    11049   Pave  None      Reg         Lvl   
34           20         70.0    10552   Pave  None      IR1         Lvl   
35          120         60.0     7313   Pave  None      Reg         Lvl   
36           60        108.0    13418   Pave  None      Reg         Lvl   
37           20        112.0    10859   Pave  None      Reg         Lvl   
38           20         74.0     8532   Pave  None      Reg         Lvl   
39           20         68.0     7922   Pave  None      Reg         Lvl   
40           90         65.0     6040   Pave  None      Reg         Lvl   
41           20         84.0     8658   Pave  None      Reg         Lvl   
42           20        115.0    16905   Pave  None      Reg         Lvl   
43           85          0.0     9180   Pave  None      IR1         Lvl   
44           20          0.0     9200   Pave  None      IR1         Lvl   
45           20         70.0     7945   Pave  None      Reg         Lvl   
46          120         61.0     7658   Pave  None      Reg         Lvl   
47           50         48.0    12822   Pave  None      IR1         Lvl   
48           20         84.0    11096   Pave  None      Reg         Lvl   
49          190         33.0     4456   Pave  None      Reg         Lvl   
50           20         66.0     7742   Pave  None      Reg         Lvl   
51           60          0.0    13869   Pave  None      IR2         Lvl   
52           50         52.0  

In [65]:
def corrplot(df, method="pearson", annot=True, **kwargs):
    df = df.pivot(df.column)
    sns.clustermap(
        df.corr(method),
        vmin=-1.0,
        vmax=1.0,
        cmap="icefire",
        method="complete",
        annot=annot,
        **kwargs,
    )


corrplot(df_train, annot=None)

ValueError: could not convert string to float: 'Pave'